# Encontro 12: Algoritmo de Girvan-Newman

Importando a biblioteca:

In [39]:
import sys
sys.path.append('..')

import socnet as sn

Configurando a biblioteca:

In [40]:
sn.graph_width = 400
sn.graph_height = 225

sn.edge_width = 1

Carregando o primeiro grafo:

In [41]:
g = sn.load_graph('teste.gml', has_pos=True)

sn.show_graph(g)

Você pode usar esse grafo para depurar sua implementação do cálculo de *edge betweenness*.

In [44]:
import queue
from math import inf, isinf


def bfs(g, s):
    q = queue.Queue()
    q.put(s)
    
    for n in g.nodes_iter():
        g.node[n]['d'] = inf
    
    g.node[s]['d'] = 0
    while not q.empty():
        curr = q.get()
        neigh = g.neighbors(curr)
        for n in neigh:
            if isinf(g.node[n]['d']):
                g.node[n]['d'] = g.node[curr]['d'] + 1
                q.put(n)


def get_final(g):
    m = [-1]
    for n in g.nodes_iter():
        if g.node[n]['fluid'] > m[0]:
            m = [n]
        elif g.node[n]['fluid'] == m[0]:
            m.append(n)
    return m

def calc_fluid(g, s):
    for i in g.nodes_iter():
        g.node[i]['fluid'] = 0
        
    q = queue.Queue()
    q.put(s)
    g.node[s]['fluid'] = 1
    visited = set()
    visited.add(s)
    
    while not q.empty():
        curr = q.get()
        neigh = g.neighbors(curr)
        for nn in neigh:
            if g.node[nn]['d'] > g.node[curr]['d']:
                # is succ
                g.node[nn]['fluid'] += g.node[curr]['fluid']
                if nn not in visited:
                    q.put(nn)
                    visited.add(nn)

def calc_edge(g):
    for n in g.nodes_iter():
        g.node[n]['f'] = 1
    
    final = get_final(g)
    q = queue.Queue()
    visited = set()
    for f in final:
        q.put(f)
        visited.add(f)
    
    while not q.empty():
        curr = q.get()
        neigh = g.neighbors(curr)
        
        for n in neigh:
            if g.node[n]['d'] < g.node[curr]['d']:
                val = (g.node[n]['fluid'] / g.node[curr]['fluid'])\
                        * g.node[curr]['f'] 
                g.edge[n][curr]['partial_betweenness'] = val
#                 print('edge[{}][{}]["partial_betweenness"] = {}'.format(
#                         n, curr, val))
                g.node[n]['f'] += val
                if n not in visited:
                    q.put(n)
                    visited.add(n)
                
                    
def calculate_partial_betweenness(g, s):

    # Esta função deve calcular o betweenness parcial de cada aresta
    # e armazenar esse valor no campo `partial_betweenness` dela.

    # Betweenness parcial significa o valor do fluxo quando um nó
    # específico é a fonte. Nesta função, esse nó é o parâmetro s.
    for i, j in g.edges_iter():
        g.edge[i][j]['partial_betweenness'] = 0
        
    bfs(g, s)
    calc_fluid(g, s)
    calc_edge(g)
#     print('fluid')
#     for n in g.nodes_iter():
#         print(n, g.node[n]['fluid'], g.node[n]['f'])
        
    
    

In [45]:
calculate_partial_betweenness(g, 0)

Carregando o segundo grafo:

In [46]:
sn.graph_width = 800
sn.graph_height = 450

g = sn.load_graph('karate.gml', has_pos=True)

sn.show_graph(g)

Construindo uma animação do Girvan-Newman:

In [47]:
from random import randrange
from queue import Queue


def snapshot(g, frames):
    frame = sn.generate_frame(g)

    frames.append(frame)


frames = []

prev_num_components = 1

gc = g.copy()

snapshot(gc, frames)

while g.edges():
    # Identifica e remove a aresta com maior betweenness.

    for n, m in g.edges():
        g.edge[n][m]['betweenness'] = 0

    for n in g.nodes():
        calculate_partial_betweenness(g, n)

        for n, m in g.edges():
            g.edge[n][m]['betweenness'] += g.edge[n][m]['partial_betweenness']

    for n, m in g.edges():
        g.edge[n][m]['betweenness'] /= 2

    n, m = max(g.edges(), key=lambda e: g.edge[e[0]][e[1]]['betweenness'])

    g.remove_edge(n, m)

    gc.edge[n][m]['color'] = (255, 255, 255)

    # Calcula o número de componentes depois da remoção.

    for n in g.nodes():
        g.node[n]['label'] = 0

    label = 0
    q = Queue()

    for s in g.nodes():
        if g.node[s]['label'] == 0:
            label += 1

            g.node[s]['label'] = label
            q.put(s)

            while not q.empty():
                n = q.get()

                for m in g.neighbors(n):
                    if g.node[m]['label'] == 0:
                        g.node[m]['label'] = label
                        q.put(m)

    num_components = label

    # Se o número de componentes aumentou, identifica as componentes por cores aleatórias.

    if prev_num_components < num_components:
        colors = {}

        for label in range(1, num_components + 1):
            colors[label] = (randrange(256), randrange(256), randrange(256))

        for n in gc.nodes():
            gc.node[n]['color'] = colors[g.node[n]['label']]

        prev_num_components = num_components

    snapshot(gc, frames)

sn.show_animation(frames)

Você não precisa modificar esse código, apenas completar o código de `calculate_partial_betweenness`.

O "gabarito" deste notebook é o vídeo `encontro12.webm` que está na mesma pasta.

In [48]:
for i, j in g.edges():
    print("edge[{}][{}]['betweenness'] = {}".format(i, j, g.edge[i][j]['betweenness']))